In [1]:
import xarray as xr
import cartopy.crs as ccrs
import cartopy.feature as cfeature
import matplotlib.pyplot as plt
import matplotlib
import os
import matplotlib.animation
import numpy as np

In [6]:
data_path = './'

# function to plot global-nest simulation
def plot_global_nest(ftype, variable, time, vmax, vmin, fig, ax):
    
    # plot global domain
    for i in range(1,7):
        file = ftype + '.tile'+str(i)+'.nc'
        f = os.path.join(data_path, file)
        ds = xr.open_dataset(f)
    
        pdata = ds[variable].isel(time = time).values
    
        file = 'grid_spec.tile'+str(i)+'.nc'
        f = os.path.join(data_path, file)
        ds_grid = xr.open_dataset(f)
    
        im = ax.pcolormesh(ds_grid.grid_lon, ds_grid.grid_lat, pdata, vmin = vmin, vmax = vmax , transform=ccrs.PlateCarree(),  cmap=plt.get_cmap('Spectral_r'))
    
    # plot nest domain
    file = ftype + '.nest02.tile7.nc'
    f = os.path.join(data_path, file)
    ds = xr.open_dataset(f)
    
    pdata = ds[variable].isel(time = time).values
    
    file = 'grid_spec.nest02.tile7.nc'
    f = os.path.join(data_path, file)
    ds_grid = xr.open_dataset(f)
    
    im = ax.pcolormesh(ds_grid.grid_lon, ds_grid.grid_lat, pdata, vmin = vmin, vmax = vmax , transform=ccrs.PlateCarree(),  cmap=plt.get_cmap('Spectral_r'), zorder=9)
    
    # plot boundaries of the nest domain
    bd_ind = [ (0, slice(None,None)), (slice(None,None), 0), (-1, slice(None,None)), (slice(None,None), -1),]
    for bd in bd_ind:
        ax.plot(ds_grid['grid_lon'].values[bd], ds_grid['grid_lat'].values[bd], 'k:' ,lw = 1.25, transform=ccrs.Geodetic(), zorder=10)

    datetimeindex = ds.indexes['time'].to_datetimeindex()
    ax.set_title('Global-nest simulation of Hurricane Ida\n' + datetimeindex[time].strftime("%Y-%m-%d %H:%M") + " UTC")
    return im

In [7]:
# Make animation
plt.rcParams["animation.html"] = "jshtml"
plt.rcParams["figure.dpi"] = 150
plt.ioff()

ftype = 'atmos_sos'
variable = 'ULWRFtoa'
vmax = 330.
vmin = 120.

# figure and map configurations
projection=ccrs.LambertConformal(central_longitude=-100, central_latitude=35, standard_parallels=[35])
fig, ax = plt.subplots(1, 1, figsize=(8, 6), dpi = 300 , subplot_kw={'projection': projection})
ax.set_extent([-135, -40, -0, 55], crs=ccrs.PlateCarree())
ax.add_feature(cfeature.BORDERS,  edgecolor='grey', linewidth=1.0, zorder=10)
ax.add_feature(cfeature.NaturalEarthFeature(
    'physical', 'coastline', '50m',
    edgecolor='grey', facecolor='none', linewidth=1.0), zorder=10)

cpb = True

def animate(t):
    global cpb
    im = plot_global_nest(ftype, variable, t, vmax, vmin, fig, ax)

    if cpb:
        cax,kw = matplotlib.colorbar.make_axes(ax,location='bottom',pad=0.05,shrink=0.8)
        cb=fig.colorbar(im,cax=cax,extend='both',**kw)
        
        cb.ax.tick_params(labelsize=8)
        cb.set_label(label = r'Outgoing longwave radiation [$\mathregular{W/m^2}$]', fontsize = 8)
        cpb = False

matplotlib.animation.FuncAnimation(fig, animate, frames = 6, interval = 1000)

/tmp/ipykernel_1530/1296954896.py:38: RuntimeWarning: Converting a CFTimeIndex with dates from a non-standard calendar, 'julian', to a pandas.DatetimeIndex, which uses dates from the standard calendar.  This may lead to subtle errors in operations that depend on the length of time between dates.
  datetimeindex = ds.indexes['time'].to_datetimeindex()
/tmp/ipykernel_1530/1296954896.py:38: RuntimeWarning: Converting a CFTimeIndex with dates from a non-standard calendar, 'julian', to a pandas.DatetimeIndex, which uses dates from the standard calendar.  This may lead to subtle errors in operations that depend on the length of time between dates.
  datetimeindex = ds.indexes['time'].to_datetimeindex()
/tmp/ipykernel_1530/1296954896.py:38: RuntimeWarning: Converting a CFTimeIndex with dates from a non-standard calendar, 'julian', to a pandas.DatetimeIndex, which uses dates from the standard calendar.  This may lead to subtle errors in operations that depend on the length of time between date